In [2]:
import pandas as pd
import requests
from threading import Thread
from queue import Queue
import logging
from bs4 import BeautifulSoup
import time

In [3]:
headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.82 Safari/537.36'}

In [4]:
df = pd.read_csv('1. dataset_filter_podla_atributov.csv')
df

name  \
0                         Australian National University   
1                                      Monash University   
2                               University of Queensland   
3                                   Macquarie University   
4                                            UNSW Sydney   
...                                                  ...   
101253                                  Pfizer (Austria)   
101254                          Neue Kantonsschule Aarau   
101255                       Radboud University Nijmegen   
101256                       Danish Geotechnical Society   
101257  Northamptonshire Healthcare NHS Foundation Trust   

                                            link        type  
0                         http://www.anu.edu.au/   Education  
1                         http://www.monash.edu/   Education  
2                          http://www.uq.edu.au/   Education  
3                              http://mq.edu.au/   Education  
4                       https://www.unsw.edu.au/   Education  
...                                          ...         ...  
101253                    https://www.pfizer.at/     Company  
101254                            http://nksa.ch   Education  
101255                 http://www.ru.nl/english/   Education  
101256  http://www.danskgeotekniskforening.dk/da       Other  
101257                  https://www.nhft.nhs.uk/  Healthcare  

[101258 rows x 3 columns]

In [5]:
url_adresy = [[i, link] for i, link in enumerate(df['link'])]
url_adresy
# len(url_adresy)

[[0, 'http://www.anu.edu.au/'],
 [1, 'http://www.monash.edu/'],
 [2, 'http://www.uq.edu.au/'],
 [3, 'http://mq.edu.au/'],
 [4, 'https://www.unsw.edu.au/'],
 [5, 'http://www.ncl.ac.uk/'],
 [6, 'https://www.uow.edu.au/index.html'],
 [7, 'http://www.unimelb.edu.au/'],
 [8, 'http://www.utas.edu.au/'],
 [9, 'http://www.adelaide.edu.au/'],
 [10, 'http://www.jcu.edu.au/'],
 [11, 'http://www.flinders.edu.au/'],
 [12, 'https://www.rmit.edu.au/'],
 [13, 'http://www.latrobe.edu.au/'],
 [14, 'http://www.vu.edu.au/'],
 [15, 'http://www.une.edu.au/'],
 [16, 'http://www.deakin.edu.au/'],
 [17, 'http://www.griffith.edu.au/'],
 [18, 'https://www.cqu.edu.au/'],
 [19, 'https://www.unisa.edu.au/'],
 [20, 'http://www.swinburne.edu.au/'],
 [21, 'http://bond.edu.au/'],
 [22, 'http://www.usc.edu.au/'],
 [23, 'http://www.csu.edu.au/'],
 [24, 'http://www.canberra.edu.au/'],
 [25, 'https://federation.edu.au/'],
 [26, 'http://www.wehi.edu.au/'],
 [27, 'http://www.cdu.edu.au/'],
 [28, 'http://www.aims.gov.au/'],
 

In [6]:
def crawl(q, results):
    while not q.empty():
        work = q.get()
        i = work[0] # index
        adresa = work[1] # URL adresa
        try:
            page = requests.get(adresa, headers=headers, timeout=5)
            if page.status_code == 200:
                # logging.info(f'{i}: {adresa}: is reachable')
                print(f'{i}: {adresa}: is reachable')
                results[i] = True

                # soup = BeautifulSoup(page.content, "html.parser")
                file_name = f"tmp//{i}.txt"
                print(file_name)
                with open(file_name, 'w') as f:
                    f.write(str(page.content))
                # for tag in tags:
                    # collection = soup.find_all(tag)
                    # print(tag + ": ", end="")
                    # print([result.text.strip().replace("\n", " ") for result in results_partial])
                    # results[i][tag] = [result.text.strip().replace("\n", " ") for result in collection if result.text.strip().replace("\n", " ")]
                    # results[i][tag] = []
                    # for result in collection:
                    #     my_string = result.text.strip().replace("\n", " ")
                    #     if my_string:
                    #         results[i][tag].append(my_string)


                # img alt - treba specialny pristup
                # results[i]['img'] = []
                # collection = soup.find_all('img')
                # for img in collection:
                #     if 'alt' in img.attrs and img.attrs['alt'] != "":
                #         results[i]['img'].append(img.attrs['alt'])

            else:
                # logging.info(f'{i}: {adresa}: is Not reachable, status_code: {my_page.status_code}')
                print(f'{i}: {adresa}: is Not reachable, status_code: {page.status_code}')
                # results[i] = False
        except requests.exceptions.RequestException as e:
            # logging.info(f'{i}: {adresa}: is Not reachable')
            print(f'{i}: {adresa}: is Not reachable')
            # results[i] = False
        q.task_done()
    return True

In [ ]:
# Vlozenie jednotlivych taskov (stranok) do radu (Queue)
threads = []
q = Queue(maxsize=0)
n_jobs = min(1000000000, len(url_adresy))

# results = [{} for x in url_adresy]
results = [False for x in url_adresy]
for i, url in url_adresy[:n_jobs]:
    q.put((i, url))


# Vykonanie taskov pomocou multithreading-u
cas = time.time()

#Starting worker threads on queue processing
for i in range(n_jobs):
    logging.debug('Starting thread ', i)
    worker = Thread(target=crawl, args=(q, results))
    worker.setDaemon(True)    #setting threads as "daemon" allows main program to exit eventually even if these dont finish correctly.
    worker.start()

#now we wait until the queue has been processed
q.join()

# logging.info('All tasks completed.')
print('All tasks completed.')

print(f"Websites checked: {n_jobs}")
print(f"Finished in {(time.time() - cas):.1f} seconds.")

In [ ]:
results

In [5]:
# Premenovanie suborov

import os

dir_path = r'tmp//'

for path in os.listdir(dir_path):
    print(path)
    new_path = path[5:]
    print(new_path)
    os.rename(dir_path + path, dir_path + new_path)

file-0.txt
0.txt
file-1.txt
1.txt
file-10.txt
10.txt
file-100.txt
100.txt
file-1000.txt
1000.txt
file-100000.txt
100000.txt
file-100001.txt
100001.txt
file-100002.txt
100002.txt
file-100003.txt
100003.txt
file-100004.txt
100004.txt
file-100005.txt
100005.txt
file-100007.txt
100007.txt
file-100008.txt
100008.txt
file-100009.txt
100009.txt
file-10001.txt
10001.txt
file-100010.txt
100010.txt
file-100012.txt
100012.txt
file-100013.txt
100013.txt
file-100014.txt
100014.txt
file-100015.txt
100015.txt
file-100016.txt
100016.txt
file-100017.txt
100017.txt
file-100018.txt
100018.txt
file-100019.txt
100019.txt
file-10002.txt
10002.txt
file-100020.txt
100020.txt
file-100021.txt
100021.txt
file-100022.txt
100022.txt
file-100023.txt
100023.txt
file-100024.txt
100024.txt
file-100025.txt
100025.txt
file-100027.txt
100027.txt
file-100028.txt
100028.txt
file-100029.txt
100029.txt
file-100030.txt
100030.txt
file-100031.txt
100031.txt
file-100032.txt
100032.txt
file-100034.txt
100034.txt
file-100035.txt


In [7]:
# Filtrovanie stranok ktore boli reachable prvy krat - mame subor

import os

dir_path = r'tmp//'

file_names = [file[:-4] for file in os.listdir(dir_path)] # nazvy suborov bez pripony - nazvov je zaroven index stranky v DataFrame

unreachable_idx = list(map(int, file_names)) #
# for f in reachable_idx[:20]:
#     print(f)

# Vytvorime masku - stranky, ktore neboli dostupne dostanu True
# Stranky, ktore sme boli schopni scrapovat dostanu False
mask = [True for i in range(df.shape[0])]
for x in unreachable_idx:
    mask[x] = False

# for x in mask[:30]:
#     print(x)

In [16]:
# Kontrola ako sa sprava maska aplikovana na DF

df[mask]

name  \
32        Baker IDI Heart and Diabetes Institute   
48                           University of Turku   
49                    Arup Group (United States)   
50                     BT Group (United Kingdom)   
65                  Pathwest Laboratory Medicine   
...                                          ...   
101222            Renown Regional Medical Center   
101232                       Mansoura University   
101235                     BML Munjal University   
101251  Verbund Katholischer Kliniken Düsseldorf   
101253                          Pfizer (Austria)   

                                                     link        type  
32                            https://www.bakeridi.edu.au   Nonprofit  
48                   http://www.utu.fi/en/Pages/home.aspx   Education  
49          http://www.arup.com/Global_locations/USA.aspx     Company  
50                                  http://www.btplc.com/     Company  
65                            http://www.pathwest.com.au/  Healthcare  
...                                                   ...         ...  
101222  https://www.renown.org/find/renown-regional-me...  Healthcare  
101232                         http://www.mans.edu.eg/en/   Education  
101235                            https://www.bml.edu.in/   Education  
101251                       http://www.vkkd-kliniken.de/  Healthcare  
101253                             https://www.pfizer.at/     Company  

[19858 rows x 3 columns]

In [24]:
# Testovanie aplikovania masky na zoznam url adries

from itertools import compress

url_adresy_new = list(compress(url_adresy, mask))
n_jobs = 1000000

for i, url in url_adresy_new[:n_jobs]:
    print(i, url)

32 https://www.bakeridi.edu.au
48 http://www.utu.fi/en/Pages/home.aspx
49 http://www.arup.com/Global_locations/USA.aspx
50 http://www.btplc.com/
65 http://www.pathwest.com.au/
67 http://www.hnehealth.nsw.gov.au/Pages/home.aspx
73 http://www.ntua.gr/index_en.html
78 http://www.oeaw.ac.at/en/austrian-academy-of-sciences/
88 http://www.unipi.gr/unipi/en/
91 http://tu-dresden.de/en
93 http://www.umcg.nl/EN
94 http://www.am.wroc.pl/en/
107 http://www.unimi.it/ENG/
115 http://www.unileon.es/en
127 https://www.uhk.cz/en-GB/UHK
138 https://www.royalholloway.ac.uk/home.aspx
145 http://www.royalmarsden.nhs.uk/pages/home.aspx
147 http://www.robosoft.com/en/home/
149 http://www.unibuc.ro/
156 http://www.ecofys.com/en/
157 https://www.tu-clausthal.de/Welcome.php.en
171 http://www.fv-berlin.de/organisation-1/history
181 http://www2.st.com/content/st_com/en.html
184 http://www.wisenmunro.org/
187 http://www.nbu.bg/entrance.php?lang=1
193 http://www.bmbf.de/en/
199 http://www.univr.it/jsp/index.jsp
20

In [ ]:
from itertools import compress

# Vytvorenie redukovaneho zoznamu stranok, ktore boli pri minulom pokuse unreachable
url_adresy_new = list(compress(url_adresy, mask))

# Vlozenie jednotlivych taskov (stranok) do radu (Queue)
threads = []
q = Queue(maxsize=0)
n_jobs = min(1000000000, len(url_adresy_new))

# results = [{} for x in url_adresy]
results = [not val for val in mask]
for i, url in url_adresy_new[:n_jobs]:
    q.put((i, url))


# Vykonanie taskov pomocou multithreading-u
cas = time.time()

#Starting worker threads on queue processing
for i in range(n_jobs):
    logging.debug('Starting thread ', i)
    worker = Thread(target=crawl, args=(q, results))
    worker.setDaemon(True)    #setting threads as "daemon" allows main program to exit eventually even if these dont finish correctly.
    worker.start()

#now we wait until the queue has been processed
q.join()

# logging.info('All tasks completed.')
print('All tasks completed.')

print(f"Websites checked: {n_jobs}")
print(f"Finished in {(time.time() - cas):.1f} seconds.")

In [ ]:
# URL = "https://realpython.github.io/fake-jobs/"
# page = requests.get(URL)
#
# # print(page.text)
# soup = BeautifulSoup(page.content, "html.parser")
# results = soup.find_all('h1')
# results